<h1 align=center><font size = 5>Segmenting and Clustering Neighborhoods in Toronto</font></h1>


## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1.  <a href="#item1">Download and Explore Dataset</a>

2.  <a href="#item2">Explore Neighborhoods in New York City</a>

3.  <a href="#item3">Analyze Each Neighborhood</a>

4.  <a href="#item4">Cluster Neighborhoods</a>

5.  <a href="#item5">Examine Clusters</a>  
    </font>
    </div>


Before we get the data and start exploring it, let's import all the dependencies that we will need.


In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files
from bs4 import BeautifulSoup # library to parse HTML

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print('Libraries imported.')

Libraries imported.


## 1. Download and Explore Dataset


Neighborhood has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood. 


For your convenience, I downloaded the files and placed it on the server, so you can simply run a `wget` command and access the data. So let's go ahead and do that.


In [11]:
fname = "toronto.html" # file with <table>
with open(fname) as fopen:
    data = fopen.read()

parse = BeautifulSoup(data, 'html.parser')
table = []
for td in parse.findAll('td'):
    if td.span.text == 'Not assigned':
        continue
    else:
        postcode = td.p.text[:3]
        borough = td.span.text.split('(')[0]
        neighborhoods = ' '.join(td.span.text.split('(')[1:]).strip(')').replace(')',' ').replace(' / ',',')
        if 'Not assigned' in neighborhoods:
            neighborhoods = borough
        #else:
        #    neighborhoods = neighborhoods.split(',')
        table.append({'postcode':postcode, 'borough':borough, 'neighborhoods':neighborhoods})
    
table = pd.DataFrame(table)
## Clean names of boroughs
table['borough']=table['borough'].replace({'Downtown TorontoStn A PO Boxes25 The Esplanade':'Downtown Toronto Stn A',
                                             'East TorontoBusiness reply mail Processing Centre969 Eastern':'East Toronto Business',
                                             'EtobicokeNorthwest':'Etobicoke Northwest','East YorkEast Toronto':'East York/East Toronto',
                                             'MississaugaCanada Post Gateway Processing Centre':'Mississauga'})

table
        

postcode                 borough  \
0        M3A              North York   
1        M4A              North York   
2        M5A        Downtown Toronto   
3        M6A              North York   
4        M7A            Queen's Park   
5        M9A               Etobicoke   
6        M1B             Scarborough   
7        M3B              North York   
8        M4B               East York   
9        M5B        Downtown Toronto   
10       M6B              North York   
11       M9B               Etobicoke   
12       M1C             Scarborough   
13       M3C              North York   
14       M4C               East York   
15       M5C        Downtown Toronto   
16       M6C                    York   
17       M9C               Etobicoke   
18       M1E             Scarborough   
19       M4E            East Toronto   
20       M5E        Downtown Toronto   
21       M6E                    York   
22       M1G             Scarborough   
23       M4G               East York   
24       M5G        Downtown Toronto   
25       M6G        Downtown Toronto   
26       M1H             Scarborough   
27       M2H              North York   
28       M3H              North York   
29       M4H               East York   
30       M5H        Downtown Toronto   
31       M6H            West Toronto   
32       M1J             Scarborough   
33       M2J              North York   
34       M3J              North York   
35       M4J  East York/East Toronto   
36       M5J        Downtown Toronto   
37       M6J            West Toronto   
38       M1K             Scarborough   
39       M2K              North York   
40       M3K              North York   
41       M4K            East Toronto   
42       M5K        Downtown Toronto   
43       M6K            West Toronto   
44       M1L             Scarborough   
45       M2L              North York   
46       M3L              North York   
47       M4L            East Toronto   
48       M5L        Downtown Toronto   
49       M6L              North York   
50       M9L              North York   
51       M1M             Scarborough   
52       M2M              North York   
53       M3M              North York   
54       M4M            East Toronto   
55       M5M              North York   
56       M6M                    York   
57       M9M              North York   
58       M1N             Scarborough   
59       M2N              North York   
60       M3N              North York   
61       M4N         Central Toronto   
62       M5N         Central Toronto   
63       M6N                    York   
64       M9N                    York   
65       M1P             Scarborough   
66       M2P              North York   
67       M4P         Central Toronto   
68       M5P         Central Toronto   
69       M6P            West Toronto   
70       M9P               Etobicoke   
71       M1R             Scarborough   
72       M2R              North York   
73       M4R         Central Toronto   
74       M5R         Central Toronto   
75       M6R            West Toronto   
76       M7R             Mississauga   
77       M9R               Etobicoke   
78       M1S             Scarborough   
79       M4S         Central Toronto   
80       M5S        Downtown Toronto   
81       M6S            West Toronto   
82       M1T             Scarborough   
83       M4T         Central Toronto   
84       M5T        Downtown Toronto   
85       M1V             Scarborough   
86       M4V         Central Toronto   
87       M5V        Downtown Toronto   
88       M8V               Etobicoke   
89       M9V               Etobicoke   
90       M1W             Scarborough   
91       M4W        Downtown Toronto   
92       M5W  Downtown Toronto Stn A   
93       M8W               Etobicoke   
94       M9W     Etobicoke Northwest   
95       M1X             Scarborough   
96       M4X        Downtown Toronto   
97       M5X        Downtown Toronto   
98       M8X               Etobicoke   
99  

#### Load and explore the data


Next, let's load the data.


In [18]:
fname = 'Geospatial_Coordinates.csv'
## Align both data frames so rows are consistent and can be merged
table = table.sort_values('postcode').reset_index().drop('index',axis=1)
coords_data = pd.read_csv(fname).sort_values('Postal Code').reset_index().drop('index',axis=1)
#print(table.tail())
#print(coords_data.tail())
table['latitude'] = coords_data['Latitude']
table['longitude'] = coords_data['Longitude']
table.shape

(103, 5)

Let's take a quick look at the data.


In [19]:
table

postcode                 borough  \
0        M1B             Scarborough   
1        M1C             Scarborough   
2        M1E             Scarborough   
3        M1G             Scarborough   
4        M1H             Scarborough   
5        M1J             Scarborough   
6        M1K             Scarborough   
7        M1L             Scarborough   
8        M1M             Scarborough   
9        M1N             Scarborough   
10       M1P             Scarborough   
11       M1R             Scarborough   
12       M1S             Scarborough   
13       M1T             Scarborough   
14       M1V             Scarborough   
15       M1W             Scarborough   
16       M1X             Scarborough   
17       M2H              North York   
18       M2J              North York   
19       M2K              North York   
20       M2L              North York   
21       M2M              North York   
22       M2N              North York   
23       M2P              North York   
24       M2R              North York   
25       M3A              North York   
26       M3B              North York   
27       M3C              North York   
28       M3H              North York   
29       M3J              North York   
30       M3K              North York   
31       M3L              North York   
32       M3M              North York   
33       M3N              North York   
34       M4A              North York   
35       M4B               East York   
36       M4C               East York   
37       M4E            East Toronto   
38       M4G               East York   
39       M4H               East York   
40       M4J  East York/East Toronto   
41       M4K            East Toronto   
42       M4L            East Toronto   
43       M4M            East Toronto   
44       M4N         Central Toronto   
45       M4P         Central Toronto   
46       M4R         Central Toronto   
47       M4S         Central Toronto   
48       M4T         Central Toronto   
49       M4V         Central Toronto   
50       M4W        Downtown Toronto   
51       M4X        Downtown Toronto   
52       M4Y        Downtown Toronto   
53       M5A        Downtown Toronto   
54       M5B        Downtown Toronto   
55       M5C        Downtown Toronto   
56       M5E        Downtown Toronto   
57       M5G        Downtown Toronto   
58       M5H        Downtown Toronto   
59       M5J        Downtown Toronto   
60       M5K        Downtown Toronto   
61       M5L        Downtown Toronto   
62       M5M              North York   
63       M5N         Central Toronto   
64       M5P         Central Toronto   
65       M5R         Central Toronto   
66       M5S        Downtown Toronto   
67       M5T        Downtown Toronto   
68       M5V        Downtown Toronto   
69       M5W  Downtown Toronto Stn A   
70       M5X        Downtown Toronto   
71       M6A              North York   
72       M6B              North York   
73       M6C                    York   
74       M6E                    York   
75       M6G        Downtown Toronto   
76       M6H            West Toronto   
77       M6J            West Toronto   
78       M6K            West Toronto   
79       M6L              North York   
80       M6M                    York   
81       M6N                    York   
82       M6P            West Toronto   
83       M6R            West Toronto   
84       M6S            West Toronto   
85       M7A            Queen's Park   
86       M7R             Mississauga   
87       M7Y   East Toronto Business   
88       M8V               Etobicoke   
89       M8W               Etobicoke   
90       M8X               Etobicoke   
91       M8Y               Etobicoke   
92       M8Z               Etobicoke   
93       M9A               Etobicoke   
94       M9B               Etobicoke   
95       M9C               Etobicoke   
96       M9L              North York   
97       M9M              North York   
98       M9N                    York   
99  

Notice how all the relevant data is in the _features_ key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.


In [5]:
neighborhoods_data = newyork_data['features']

Let's take a look at the first item in this list.


In [6]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Tranform the data into a _pandas_ dataframe


The next task is essentially transforming this data of nested Python dictionaries into a _pandas_ dataframe. So let's start by creating an empty dataframe.


In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Take a look at the empty dataframe to confirm that the columns are as intended.


In [8]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.


In [9]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe.


In [10]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

And make sure that the dataset has all 5 boroughs and 306 neighborhoods.


In [11]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.


In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>ny_explorer</em>, as shown below.


In [4]:
address = 'Scarborough, Toronto, Ontario, Canada'

geolocator = Nominatim(user_agent="ontario_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Scarborough are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Scarborough are 43.7729744, -79.2576479.


#### Create a map of New York with neighborhoods superimposed on top.


In [14]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    color = 'yellow'
    if borough == 'Bronx': color = 'red'
    elif borough == 'Queens': color = 'blue'
    elif borough == 'Staten Island': color = 'green'
    elif borough == 'Brooklyn': color = 'orange'
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color=color,
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

**Folium** is a great visualization library. Feel free to zoom into the above map, and click on each circle mark to reveal the name of the neighborhood and its respective borough.


However, for illustration purposes, let's simplify the above map and segment and cluster only the neighborhoods in Manhattan. So let's slice the original dataframe and create a new dataframe of the Manhattan data.


In [15]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

Let's get the geographical coordinates of Manhattan.


In [16]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


As we did with all of New York City, let's visualizat Manhattan the neighborhoods in it.


In [17]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.


#### Define Foursquare Credentials and Version


In [18]:
with open('.fs_client_id') as fopen:
    CLIENT_ID = fopen.read().strip() # your Foursquare ID
with open('.fs_client_secret') as fopen:
    CLIENT_SECRET = fopen.read().strip() # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 45G3AFA1RMWI5ZBGA1CNMWIANV2IKBMQZ2055Q3FY4UFUWZ0
CLIENT_SECRET:CXGDLJOHSB3LKYZ2RIGELH5C2RS4L2CLRJHDWYLY4F1KO32S


#### Let's explore the first neighborhood in our dataframe.


Get the neighborhood's name.


In [19]:
manhattan_data.loc[0, 'Neighborhood']

'Marble Hill'

Get the neighborhood's latitude and longitude values.


In [20]:
neighborhood_latitude = manhattan_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = manhattan_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = manhattan_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Marble Hill are 40.87655077879964, -73.91065965862981.


#### Now, let's get the top 100 venues that are in Marble Hill within a radius of 500 meters.


First, let's create the GET request URL. Name your URL **url**.


In [21]:
# type your answer here
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, neighborhood_latitude, neighborhood_longitude, VERSION, radius, LIMIT) 
url


'https://api.foursquare.com/v2/venues/explore?client_id=45G3AFA1RMWI5ZBGA1CNMWIANV2IKBMQZ2055Q3FY4UFUWZ0&client_secret=CXGDLJOHSB3LKYZ2RIGELH5C2RS4L2CLRJHDWYLY4F1KO32S&ll=40.87655077879964,-73.91065965862981&v=20180605&radius=500&limit=100'

Double-click **here** for the solution.

<!-- The correct answer is:
LIMIT = 100 # limit of number of venues returned by Foursquare API
-->

<!--
radius = 500 # define radius
-->

<!--
\\\\ # create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL
--> 


Send the GET request and examine the resutls


In [22]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '6100682a597c21345e7574e7'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Marble Hill',
  'headerFullLocation': 'Marble Hill, New York',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 23,
  'suggestedBounds': {'ne': {'lat': 40.88105078329964,
    'lng': -73.90471933917806},
   'sw': {'lat': 40.87205077429964, 'lng': -73.91659997808156}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b4429abf964a52037f225e3',
       'name': "Arturo's",
       'location': {'address': '5198 Broadway',
        'crossStreet': 'at 225th St.',
        'lat': 40.87441177110231,
        'lng': -73.91027100981574,
        'labeledLatLngs': [{'label'

From the Foursquare lab in the previous module, we know that all the information is in the _items_ key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.


In [23]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a _pandas_ dataframe.


In [30]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()


name   categories        lat        lng
0       Arturo's  Pizza Place  40.874412 -73.910271
1    Bikram Yoga  Yoga Studio  40.876844 -73.906204
2  Tibbett Diner        Diner  40.880404 -73.908937
3        Dunkin'   Donut Shop  40.877136 -73.906666
4      Starbucks  Coffee Shop  40.877531 -73.905582

And how many venues were returned by Foursquare?


In [29]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

23 venues were returned by Foursquare.


## 2. Explore Neighborhoods in Manhattan


#### Let's create a function to repeat the same process to all the neighborhoods in Manhattan


In [31]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called _manhattan_venues_.


In [37]:
# type your answer here
manhattan_venues = getNearbyVenues( manhattan_data['Neighborhood'], manhattan_data['Latitude'], manhattan_data['Longitude'], radius = 1000)
manhattan_venues

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0             Marble Hill              40.876551              -73.910660   
1             Marble Hill              40.876551              -73.910660   
2             Marble Hill              40.876551              -73.910660   
3             Marble Hill              40.876551              -73.910660   
4             Marble Hill              40.876551              -73.910660   
5             Marble Hill              40.876551              -73.910660   
6             Marble Hill              40.876551              -73.910660   
7             Marble Hill              40.876551              -73.910660   
8             Marble Hill              40.876551              -73.910660   
9             Marble Hill              40.876551              -73.910660   
10            Marble Hill              40.876551              -73.910660   
11            Marble Hill              40.876551              -73.910660   
12            Marble Hill              40.876551              -73.910660   
13            Marble Hill              40.876551              -73.910660   
14            Marble Hill              40.876551              -73.910660   
15            Marble Hill              40.876551              -73.910660   
16            Marble Hill              40.876551              -73.910660   
17            Marble Hill              40.876551              -73.910660   
18            Marble Hill              40.876551              -73.910660   
19            Marble Hill              40.876551              -73.910660   
20            Marble Hill              40.876551              -73.910660   
21            Marble Hill              40.876551              -73.910660   
22            Marble Hill              40.876551              -73.910660   
23            Marble Hill              40.876551              -73.910660   
24            Marble Hill              40.876551              -73.910660   
25            Marble Hill              40.876551              -73.910660   
26            Marble Hill              40.876551              -73.910660   
27            Marble Hill              40.876551              -73.910660   
28            Marble Hill              40.876551              -73.910660   
29            Marble Hill              40.876551              -73.910660   
30            Marble Hill              40.876551              -73.910660   
31            Marble Hill              40.876551              -73.910660   
32            Marble Hill              40.876551              -73.910660   
33            Marble Hill              40.876551              -73.910660   
34            Marble Hill              40.876551              -73.910660   
35            Marble Hill              40.876551              -73.910660   
36            Marble Hill              40.876551              -73.910660   
37            Marble Hill              40.876551              -73.910660   
38            Marble Hill              40.876551              -73.910660   
39            Marble Hill              40.876551              -73.910660   
40            Marble Hill              40.876551              -73.910660   
41            Marble Hill              40.876551              -73.910660   
42            Marble Hill              40.876551              -73.910660   
43            Marble Hill              40.876551              -73.910660   
44            Marble Hill              40.876551              -73.910660   
45            Marble Hill              40.876551              -73.910660   
46            Marble Hill              40.876551              -73.910660   
47            Marble Hill              40.876551              -73.910660   
48            Marble Hill              40.876551              -73.910660   
49            Marble Hill              40.876551              -73.910660   
50            Marble Hill              40.876551              -73.910660   
51            Marble Hill              40.876551             

Double-click **here** for the solution.

<!-- The correct answer is:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )
--> 


#### Let's check the size of the resulting dataframe


In [38]:
print(manhattan_venues.shape)
manhattan_venues.head()

(3980, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066    Bikram Yoga   
1  Marble Hill              40.876551               -73.91066       Arturo's   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066    Sam's Pizza   
4  Marble Hill              40.876551               -73.91066      Starbucks   

   Venue Latitude  Venue Longitude Venue Category  
0       40.876844       -73.906204    Yoga Studio  
1       40.874412       -73.910271    Pizza Place  
2       40.880404       -73.908937          Diner  
3       40.879435       -73.905859    Pizza Place  
4       40.877531       -73.905582    Coffee Shop

Let's check how many venues were returned for each neighborhood


In [39]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                      100                     100    100   
Carnegie Hill                          100                     100    100   
Central Harlem                         100                     100    100   
Chelsea                                100                     100    100   
Chinatown                              100                     100    100   
Civic Center                           100                     100    100   
Clinton                                100                     100    100   
East Harlem                            100                     100    100   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Gramercy                               100                     100    100   
Greenwich Village                      100                     100    100   
Hamilton Heights                       100                     100    100   
Hudson Yards                           100                     100    100   
Inwood                                 100                     100    100   
Lenox Hill                             100                     100    100   
Lincoln Square                         100                     100    100   
Little Italy                           100                     100    100   
Lower East Side                        100                     100    100   
Manhattan Valley                       100                     100    100   
Manhattanville                         100                     100    100   
Marble Hill                             80                      80     80   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                    100                     100    100   
Murray Hill                            100                     100    100   
Noho                                   100                     100    100   
Roosevelt Island                       100                     100    100   
Soho                                   100                     100    100   
Stuyvesant Town                        100                     100    100   
Sutton Place                           100                     100    100   
Tribeca                                100                     100    100   
Tudor City                             100                     100    100   
Turtle Bay                             100                     100    100   
Upper East Side                        100                     100    100   
Upper West Side                        100                     100    100   
Washington Heights                     100                     100    100   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City               100              100             100  
Carnegie Hill                   100              100             100  
Central Harlem                  100              100             100  
Chelsea                         100              100             100  
Chinatown                       100              100             100  
Civic Center                    100              100             100  
Clinton                         100              100             100  
East Harlem                     100              100             100  
East Village                    100              100             100  
Finan

#### Let's find out how many unique categories can be curated from all the returned venues


In [40]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 310 uniques categories.


## 3. Analyze Each Neighborhood


In [44]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  African Restaurant  \
0  Marble Hill                  0               0                   0   
1  Marble Hill                  0               0                   0   
2  Marble Hill                  0               0                   0   
3  Marble Hill                  0               0                   0   
4  Marble Hill                  0               0                   0   

   American Restaurant  Animal Shelter  Antique Shop  Argentinian Restaurant  \
0                    0               0             0                       0   
1                    0               0             0                       0   
2                    0               0             0                       0   
3                    0               0             0                       0   
4                    0               0             0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0            0           0                    0                 0   
1            0           0                    0                 0   
2            0           0                    0                 0   
3            0           0                    0                 0   
4            0           0                    0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Court  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Basketball Stadium  Beach  Beer Bar  Beer Garden  Beer Store  \
0                   0      0         0            0           0   
1                   0      0         0            0           0   
2                   0      0         0            0           0   
3                   0      0         0            0           0   
4                   0      0         0            0           0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  Breakfast Spot  \
0          0         0           0                     0               0   
1          0         0           0                     0               0   
2          0         0           0                     0               0   
3          0         0           0                     0               0   
4          0         0           0                     0               0   

   Bridal Shop  Bridge  Bubble Tea Shop  Building  Burger Joint  \
0            0       0                0         0             0   
1            0       0                0         0             0   
2            0       0                0         0             0   
3            0       0                0         0             0   
4            0       0                0         0    

And let's examine the new dataframe size.


In [45]:
manhattan_onehot.shape

(3980, 311)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category


In [46]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Adult Boutique  \
0     Battery Park City               0.00            0.00   
1         Carnegie Hill               0.00            0.00   
2        Central Harlem               0.00            0.00   
3               Chelsea               0.00            0.00   
4             Chinatown               0.00            0.00   
5          Civic Center               0.00            0.00   
6               Clinton               0.00            0.00   
7           East Harlem               0.00            0.00   
8          East Village               0.00            0.00   
9    Financial District               0.00            0.00   
10             Flatiron               0.00            0.00   
11             Gramercy               0.00            0.00   
12    Greenwich Village               0.00            0.00   
13     Hamilton Heights               0.00            0.01   
14         Hudson Yards               0.00            0.00   
15               Inwood               0.00            0.00   
16           Lenox Hill               0.00            0.00   
17       Lincoln Square               0.00            0.00   
18         Little Italy               0.00            0.00   
19      Lower East Side               0.00            0.00   
20     Manhattan Valley               0.00            0.00   
21       Manhattanville               0.00            0.01   
22          Marble Hill               0.00            0.00   
23              Midtown               0.00            0.00   
24        Midtown South               0.00            0.00   
25  Morningside Heights               0.00            0.00   
26          Murray Hill               0.00            0.00   
27                 Noho               0.00            0.00   
28     Roosevelt Island               0.00            0.00   
29                 Soho               0.00            0.00   
30      Stuyvesant Town               0.00            0.00   
31         Sutton Place               0.01            0.01   
32              Tribeca               0.00            0.00   
33           Tudor City               0.00            0.00   
34           Turtle Bay               0.00            0.00   
35      Upper East Side               0.00            0.00   
36      Upper West Side               0.01            0.00   
37   Washington Heights               0.01            0.00   
38         West Village               0.00            0.00   
39            Yorkville               0.00            0.00   

    African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0                 0.00                 0.02            0.00          0.01   
1                 0.00                 0.02            0.01          0.00   
2                 0.04                 0.03            0.00          0.00   
3                 0.00                 0.02            0.00          0.00   
4                 0.00                 0.02            0.00          0.00   
5                 0.00                 0.04            0.00          0.01   
6                 0.00                 0.03            0.00          0.00   
7                 0.01                 0.01            0.00          0.00   
8                 0.00                 0.01            0.00          0.00   
9                 0.00                 0.04            0.00          0.00   
10                0.00                 0.03            0.00          0.00   
11                0.00                 0.04            0.00          0.00   
12                0.00                 0.03            0.00          0.00   
13                0.01                 0.02            0.00          0.00   
14                0.00                 0.03            0.00          0.00   
15                0.00                 0.01            0.00          0.00   
16                0.00                 0.02            0.00          0.00   
17                0.00                 0.03            0.00          0.00   
18   

#### Let's confirm the new size


In [47]:
manhattan_grouped.shape

(40, 311)

#### Let's print each neighborhood along with the top 5 most common venues


In [49]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 3})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
         venue  freq
0         Park  0.09
1  Coffee Shop  0.06
2        Hotel  0.04
3   Playground  0.03
4          Gym  0.03


----Carnegie Hill----
                  venue  freq
0                  Café  0.05
1           Coffee Shop  0.05
2  Gym / Fitness Center  0.05
3                Bakery  0.04
4           Yoga Studio  0.03


----Central Harlem----
                             venue  freq
0                             Café  0.05
1  Southern / Soul Food Restaurant  0.05
2               African Restaurant  0.04
3                     Cocktail Bar  0.03
4                              Bar  0.03


----Chelsea----
                     venue  freq
0              Art Gallery  0.11
1              Coffee Shop  0.05
2  New American Restaurant  0.03
3                   Bakery  0.03
4       Seafood Restaurant  0.03


----Chinatown----
                venue  freq
0              Bakery  0.05
1        Cocktail Bar  0.05
2         Coffee Shop  0.05
3      Ice Cream Shop  0.

#### Let's put that into a _pandas_ dataframe


First, let's write a function to sort the venues in descending order.


In [50]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.


In [53]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()


Neighborhood            1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                             Park           Coffee Shop   
1      Carnegie Hill                             Café  Gym / Fitness Center   
2     Central Harlem  Southern / Soul Food Restaurant                  Café   
3            Chelsea                      Art Gallery           Coffee Shop   
4          Chinatown                     Cocktail Bar           Coffee Shop   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                    Hotel             Wine Shop            Playground   
1              Coffee Shop                Bakery          Cocktail Bar   
2       African Restaurant           Pizza Place     French Restaurant   
3  New American Restaurant    Seafood Restaurant               Theater   
4                   Bakery        Ice Cream Shop                  Café   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                 Plaza                   Gym        Sandwich Place   
1             Bookstore                   Bar                   Gym   
2    Seafood Restaurant          Cocktail Bar                   Bar   
3                Bakery                  Café             Roof Deck   
4              Wine Bar    Chinese Restaurant        Sandwich Place   

  9th Most Common Venue 10th Most Common Venue  
0           Pizza Place           Burger Joint  
1            Art Museum            Yoga Studio  
2                Lounge    American Restaurant  
3      Tapas Restaurant               Beer Bar  
4          Optical Shop       Asian Restaurant

## 4. Cluster Neighborhoods


Run _k_-means to cluster the neighborhood into 5 clusters.


In [57]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([4, 1, 4, 3, 3, 3, 2, 4, 1, 1, 3, 1, 3, 4, 2, 4, 1, 2, 3, 1, 4, 4,
       4, 2, 3, 4, 3, 3, 4, 3, 1, 1, 3, 4, 4, 0, 1, 4, 1, 1], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.


In [58]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

ValueError: cannot insert Cluster Labels, already exists

In [59]:
manhattan_merged

Borough         Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Manhattan          Marble Hill  40.876551 -73.910660               4   
1   Manhattan            Chinatown  40.715618 -73.994279               3   
2   Manhattan   Washington Heights  40.851903 -73.936900               4   
3   Manhattan               Inwood  40.867684 -73.921210               4   
4   Manhattan     Hamilton Heights  40.823604 -73.949688               4   
5   Manhattan       Manhattanville  40.816934 -73.957385               4   
6   Manhattan       Central Harlem  40.815976 -73.943211               4   
7   Manhattan          East Harlem  40.792249 -73.944182               4   
8   Manhattan      Upper East Side  40.775639 -73.960508               0   
9   Manhattan            Yorkville  40.775930 -73.947118               1   
10  Manhattan           Lenox Hill  40.768113 -73.958860               1   
11  Manhattan     Roosevelt Island  40.762160 -73.949168               4   
12  Manhattan      Upper West Side  40.787658 -73.977059               1   
13  Manhattan       Lincoln Square  40.773529 -73.985338               2   
14  Manhattan              Clinton  40.759101 -73.996119               2   
15  Manhattan              Midtown  40.754691 -73.981669               2   
16  Manhattan          Murray Hill  40.748303 -73.978332               3   
17  Manhattan              Chelsea  40.744035 -74.003116               3   
18  Manhattan    Greenwich Village  40.726933 -73.999914               3   
19  Manhattan         East Village  40.727847 -73.982226               1   
20  Manhattan      Lower East Side  40.717807 -73.980890               1   
21  Manhattan              Tribeca  40.721522 -74.010683               3   
22  Manhattan         Little Italy  40.719324 -73.997305               3   
23  Manhattan                 Soho  40.722184 -74.000657               3   
24  Manhattan         West Village  40.734434 -74.006180               1   
25  Manhattan     Manhattan Valley  40.797307 -73.964286               4   
26  Manhattan  Morningside Heights  40.808000 -73.963896               4   
27  Manhattan             Gramercy  40.737210 -73.981376               1   
28  Manhattan    Battery Park City  40.711932 -74.016869               4   
29  Manhattan   Financial District  40.707107 -74.010665               1   
30  Manhattan        Carnegie Hill  40.782683 -73.953256               1   
31  Manhattan                 Noho  40.723259 -73.988434               3   
32  Manhattan         Civic Center  40.715229 -74.005415               3   
33  Manhattan        Midtown South  40.748510 -73.988713               3   
34  Manhattan         Sutton Place  40.760280 -73.963556               1   
35  Manhattan           Turtle Bay  40.752042 -73.967708               4   
36  Manhattan           Tudor City  40.746917 -73.971219               4   
37  Manhattan      Stuyvesant Town  40.731000 -73.974052               1   
38  Manhattan             Flatiron  40.739673 -73.990947               3   
39  Manhattan         Hudson Yards  40.756658 -74.000111               2   

              1st Most Common Venue 2nd Most Common Venue  \
0                              Park    Mexican Restaurant   
1                      Cocktail Bar           Coffee Shop   
2                       Pizza Place                  Café   
3         Latin American Restaurant         Deli / Bodega   
4                       Coffee Shop    Mexican Restaurant   
5                              Park           Coffee Shop   
6   Southern / Soul Food Restaurant                  Café   
7                            Bakery                  Café   
8                           Exhibit    Italian Restaurant   
9                    Ice Cream Shop    Italian Restaurant   
10               Italian Restaurant      Sushi Restaurant   
11                             Park      Sushi Restaurant   
12               Italian Restaurant                Bakery   
13                French Restaurant

Finally, let's visualize the resulting clusters


In [56]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>


## 5. Examine Clusters


Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.


#### Cluster 1


In [60]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
8  Upper East Side               Exhibit    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
8  Gym / Fitness Center                Bakery           Coffee Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8                 Hotel   American Restaurant    Spanish Restaurant   

  9th Most Common Venue 10th Most Common Venue  
8                   Spa     Seafood Restaurant

#### Cluster 2


In [61]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood    1st Most Common Venue 2nd Most Common Venue  \
9            Yorkville           Ice Cream Shop    Italian Restaurant   
10          Lenox Hill       Italian Restaurant      Sushi Restaurant   
12     Upper West Side       Italian Restaurant                Bakery   
19        East Village                 Wine Bar          Dessert Shop   
20     Lower East Side              Pizza Place                  Café   
24        West Village       Italian Restaurant                  Park   
27            Gramercy  New American Restaurant    Italian Restaurant   
29  Financial District              Coffee Shop           Pizza Place   
30       Carnegie Hill                     Café  Gym / Fitness Center   
34        Sutton Place                      Gym                Bakery   
37     Stuyvesant Town                      Bar           Pizza Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
9              Wine Shop           Coffee Shop                   Gym   
10  Gym / Fitness Center          Cocktail Bar                   Gym   
12                  Café           Coffee Shop        Ice Cream Shop   
19           Coffee Shop                   Bar        Ice Cream Shop   
20                Bakery             Wine Shop      Asian Restaurant   
24           Coffee Shop   American Restaurant          Cocktail Bar   
27    Mexican Restaurant   American Restaurant           Coffee Shop   
29   American Restaurant                 Hotel          Cocktail Bar   
30           Coffee Shop                Bakery          Cocktail Bar   
34     Indian Restaurant    Italian Restaurant                  Park   
37                  Park           Coffee Shop    Italian Restaurant   

   6th Most Common Venue     7th Most Common Venue 8th Most Common Venue  \
9                    Bar        Mexican Restaurant            Bagel Shop   
10         Women's Store         French Restaurant        Clothing Store   
12                   Gym                      Park   American Restaurant   
19   Japanese Restaurant               Pizza Place                Garden   
20     French Restaurant        Italian Restaurant          Cocktail Bar   
24     French Restaurant   New American Restaurant              Wine Bar   
27             Juice Bar  Mediterranean Restaurant     Indian Restaurant   
29         Memorial Site                     Plaza    Italian Restaurant   
30             Bookstore                       Bar                   Gym   
34  Gym / Fitness Center                       Spa     French Restaurant   
37          Cocktail Bar                Bagel Shop             Wine Shop   

       9th Most Common Venue 10th Most Common Venue  
9                Pizza Place          Deli / Bodega  
10               Pizza Place             Taco Place  
12                  Wine Bar             Bagel Shop  
19         Korean Restaurant                   Park  
20                Food Court               Sake Bar  
24                Steakhouse              Speakeasy  
27                      Park                   Café  
29                Steakhouse    Monument / Landmark  
30                Art Museum            Yoga Studio  
34  Mediterranean Restaurant     Salon / Barbershop  
37       American Restaurant    Japanese Restaurant

#### Cluster 3


In [62]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
13  Lincoln Square     French Restaurant               Theater   
14         Clinton               Theater             Wine Shop   
15         Midtown               Theater                 Plaza   
39    Hudson Yards  Gym / Fitness Center               Theater   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
13           Coffee Shop    Italian Restaurant                 Plaza   
14  Gym / Fitness Center                 Hotel                   Bar   
15                 Hotel        Sandwich Place            Steakhouse   
39                 Hotel    Italian Restaurant           Coffee Shop   

   6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
13          Concert Hall  Performing Arts Venue      Sushi Restaurant   
14           Coffee Shop           Burger Joint    Italian Restaurant   
15   American Restaurant       Sushi Restaurant                   Gym   
39         Indie Theater    American Restaurant           Art Gallery   

   9th Most Common Venue 10th Most Common Venue  
13  Gym / Fitness Center    American Restaurant  
14                  Park                    Gym  
15           Coffee Shop          Grocery Store  
39                   Gym                 Lounge

#### Cluster 4


In [63]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
1           Chinatown          Cocktail Bar           Coffee Shop   
16        Murray Hill     Korean Restaurant   Japanese Restaurant   
17            Chelsea           Art Gallery           Coffee Shop   
18  Greenwich Village    Italian Restaurant                   Spa   
21            Tribeca                  Park                 Hotel   
22       Little Italy        Clothing Store          Cocktail Bar   
23               Soho        Clothing Store                Bakery   
31               Noho          Cocktail Bar                 Hotel   
32       Civic Center           Coffee Shop     French Restaurant   
33      Midtown South     Korean Restaurant  Gym / Fitness Center   
38           Flatiron  Gym / Fitness Center           Yoga Studio   

      3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
1                    Bakery        Ice Cream Shop                    Café   
16     Gym / Fitness Center                 Hotel             Coffee Shop   
17  New American Restaurant    Seafood Restaurant                 Theater   
18              Coffee Shop      Sushi Restaurant          Sandwich Place   
21       Italian Restaurant                   Spa             Coffee Shop   
22                    Hotel            Shoe Store                  Bakery   
23       Italian Restaurant           Coffee Shop          Cosmetics Shop   
31      Japanese Restaurant    Italian Restaurant        Asian Restaurant   
32       Chinese Restaurant                 Hotel     American Restaurant   
33                    Hotel           Coffee Shop                  Bakery   
38  New American Restaurant                 Hotel  Furniture / Home Store   

   6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
1               Wine Bar     Chinese Restaurant        Sandwich Place   
16          Gourmet Shop                 Bakery           Pizza Place   
17                Bakery                   Café             Roof Deck   
18   American Restaurant            Pizza Place        Clothing Store   
21                  Café      French Restaurant           Men's Store   
22              Wine Bar         Sandwich Place    Salon / Barbershop   
23    Salon / Barbershop                   Café     French Restaurant   
31              Wine Bar  Vietnamese Restaurant             Bookstore   
32                  Café            Men's Store                Bakery   
33          Dessert Shop    American Restaurant    Italian Restaurant   
38                  Park    American Restaurant                  Café   

   9th Most Common Venue           10th Most Common Venue  
1           Optical Shop                 Asian Restaurant  
16      Sushi Restaurant                     Burger Joint  
17      Tapas Restaurant                         Beer Bar  
18    Salon / Barbershop               Seafood Restaurant  
21             Wine Shop                         Wine Bar  
22           Art Gallery                 Asian Restaurant  
23                 Hotel                      Pizza Place  
31           Pizza Place  Southern / Soul Food Restaurant  
32  Gym / Fitness Center                 Asian Restaurant  
33        Sandwich Place              Japanese Restaurant  
38      Toy / Game Store              Japanese Restaurant

#### Cluster 5


In [64]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood            1st Most Common Venue  \
0           Marble Hill                             Park   
2    Washington Heights                      Pizza Place   
3                Inwood        Latin American Restaurant   
4      Hamilton Heights                      Coffee Shop   
5        Manhattanville                             Park   
6        Central Harlem  Southern / Soul Food Restaurant   
7           East Harlem                           Bakery   
11     Roosevelt Island                             Park   
25     Manhattan Valley                    Grocery Store   
26  Morningside Heights                      Coffee Shop   
28    Battery Park City                             Park   
35           Turtle Bay                      Coffee Shop   
36           Tudor City                      Coffee Shop   

   2nd Most Common Venue      3rd Most Common Venue 4th Most Common Venue  \
0     Mexican Restaurant                       Café           Pizza Place   
2                   Café  Latin American Restaurant                Bakery   
3          Deli / Bodega         Mexican Restaurant            Restaurant   
4     Mexican Restaurant                        Bar                  Café   
5            Coffee Shop        American Restaurant    Mexican Restaurant   
6                   Café         African Restaurant           Pizza Place   
7                   Café                Pizza Place    Mexican Restaurant   
11      Sushi Restaurant                Coffee Shop                  Café   
25           Coffee Shop         Mexican Restaurant        Ice Cream Shop   
26   American Restaurant         Italian Restaurant                  Park   
28           Coffee Shop                      Hotel             Wine Shop   
35                  Park        Japanese Restaurant    Seafood Restaurant   
36   Japanese Restaurant              Grocery Store           Pizza Place   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0     Spanish Restaurant           Supermarket        Sandwich Place   
2     Spanish Restaurant           Coffee Shop      Tapas Restaurant   
3            Pizza Place              Wine Bar                  Café   
4                   Park          Cocktail Bar      Sushi Restaurant   
5     Italian Restaurant    Seafood Restaurant                  Café   
6      French Restaurant    Seafood Restaurant          Cocktail Bar   
7        Thai Restaurant         Deli / Bodega          Cocktail Bar   
11      Greek Restaurant          Cocktail Bar          Tennis Court   
25                  Park                   Bar     Indian Restaurant   
26             Bookstore    Chinese Restaurant                Bakery   
28            Playground                 Plaza                   Gym   
35      Sushi Restaurant              Wine Bar   American Restaurant   
36                  Park      Sushi Restaurant            Taco Place   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0             Donut Shop    Chinese Restaurant                 Bakery  
2                   Park     Mobile Phone Shop     Mexican Restaurant  
3                   Park                Bakery     Spanish Restaurant  
4            Yoga Studio     Indian Restaurant                 Bakery  
5     Chinese Restaurant          Cocktail Bar                Theater  
6                    Bar                Lounge    American Restaurant  
7                    Gym              Fountain     Italian Restaurant  
11           Pizza Place                 Hotel            Salad Place  
25   Japanese Restaurant            Bagel Shop     Chinese Restaurant  
26            Playground    Mexican Restaurant         Farmers Market  
28        Sandwich Place           Pizza Place           Burger Joint  
35                Bakery      Greek Restaurant            Pizza Place  
36                   Gym             Juice Bar            Salad Place

### Thank you for completing this lab!

This notebook was created by [Alex Aklson](https://www.linkedin.com/in/aklson?cm_mmc=Email_Newsletter-_-Developer_Ed%2BTech-_-WW_WW-_-SkillsNetwork-Courses-IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork-21253531&cm_mmca1=000026UJ&cm_mmca2=10006555&cm_mmca3=M12345678&cvosrc=email.Newsletter.M12345678&cvo_campaign=000026UJ&cm_mmc=Email_Newsletter-_-Developer_Ed%2BTech-_-WW_WW-_-SkillsNetwork-Courses-IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork-21253531&cm_mmca1=000026UJ&cm_mmca2=10006555&cm_mmca3=M12345678&cvosrc=email.Newsletter.M12345678&cvo_campaign=000026UJ) and [Polong Lin](https://www.linkedin.com/in/polonglin?cm_mmc=Email_Newsletter-_-Developer_Ed%2BTech-_-WW_WW-_-SkillsNetwork-Courses-IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork-21253531&cm_mmca1=000026UJ&cm_mmca2=10006555&cm_mmca3=M12345678&cvosrc=email.Newsletter.M12345678&cvo_campaign=000026UJ&cm_mmc=Email_Newsletter-_-Developer_Ed%2BTech-_-WW_WW-_-SkillsNetwork-Courses-IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork-21253531&cm_mmca1=000026UJ&cm_mmca2=10006555&cm_mmca3=M12345678&cvosrc=email.Newsletter.M12345678&cvo_campaign=000026UJ). I hope you found this lab interesting and educational. Feel free to contact us if you have any questions!


This notebook is part of a course on **Coursera** called _Applied Data Science Capstone_. If you accessed this notebook outside the course, you can take this course online by clicking [here](http://cocl.us/DP0701EN_Coursera_Week3_LAB2).


## Change Log

| Date (YYYY-MM-DD) | Version | Changed By    | Change Description         |
| ----------------- | ------- | ------------- | -------------------------- |
| 2020-11-26        | 2.0     | Lakshmi Holla | Updated the markdown cells |
|                   |         |               |                            |
|                   |         |               |                            |

## <h3 align="center"> © IBM Corporation 2020. All rights reserved. <h3/>
